In [1]:
import json
import pandas as pd
import numpy as np
import seaborn as sns
import tensorflow_probability as tfp
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import gaussian_kde

import sys

sys.path.append("/Users/jay/Desktop/Bachelorarbeit/Implementation")
from dependencies.hbv_sask.model import HBVSASKModel as hbvmodel
from src.execute_model import run_model_single_parameter_node
from src.construct_model import get_model

ndims = 7
dims = ["TT", "C0", "beta", "ETF", "FC", "FRAC", "K2"]
colors = sns.color_palette(n_colors=ndims)

model_long = get_model("/Users/jay/Desktop/Bachelorarbeit/Implementation/configurations/benchmark_configs/test_oldman_long.json", "Oldman_Basin")
model_short = get_model("/Users/jay/Desktop/Bachelorarbeit/Implementation/configurations/benchmark_configs/test_oldman_short.json", "Oldman_Basin")
model_banff = get_model("/Users/jay/Desktop/Bachelorarbeit/Implementation/configurations/benchmark_configs/test_banff.json", "Banff_Basin")

all_files = ['short_no_floods.txt', 'short_floods.txt', 'long_no_floods.txt', 'long_floods.txt', 'oldman_train.txt', 'banff_train.txt', 'su25.txt', 'su50.txt', 'su100.txt']
for i in range(len(all_files)):
    all_files[i] = f'data/{all_files[i]}'
time_series_name = ['Short and Calm (Oldman)', 'Short with Peaks (Oldman)', 'Long and Calm (Oldman)', 'Long with Peaks (Oldman)', '97-03 (Oldman)', '97-03 (Banff)', 'Spin-up 25%', 'Spin-up 50%', 'Spin-up 100%']


start_date: 1992-01-01 00:00:00
start_date_predictions: 1993-12-31 00:00:00
end_date: 1995-12-30 00:00:00
simulation length: 729
full_data_range is 1460 hours including spin_up_length of 730 hours
simulation_range is of length 730 hours
start_date: 2003-01-01 00:00:00
start_date_predictions: 2003-12-31 00:00:00
end_date: 2004-12-30 00:00:00
simulation length: 365
full_data_range is 730 hours including spin_up_length of 364 hours
simulation_range is of length 366 hours
start_date: 1992-01-01 00:00:00
start_date_predictions: 1993-12-31 00:00:00
end_date: 1995-12-30 00:00:00
simulation length: 729
full_data_range is 1460 hours including spin_up_length of 730 hours
simulation_range is of length 730 hours


In [2]:
def viz_long(input_file, time_series_name):
    # Construct params
    configurationObject = model_long.configurationObject
    param_lower = []
    param_upper = []
    for param in configurationObject["parameters"]:
        if param["distribution"] == "Uniform":
            param_lower.append(param["lower"])
            param_upper.append(param["upper"])
        else:
            raise NotImplementedError(
                f"Sorry, the distribution {param['distribution']} is not supported yet"
            )
    param_lower = np.array(param_lower)
    param_upper = np.array(param_upper)

    samples = pd.read_csv(f"{input_file}")

    # Sampling Max
    param_vec = []
    for i in range(len(samples.loc[0])):
        values, counts = np.unique(samples.iloc[:, i], return_counts=True)
        ind = np.argmax(counts)
        param_vec.append(values[ind])

    _, posterior_max, _, _ = run_model_single_parameter_node(model_long, param_vec)

    # Posterior Mean
    sample_param = []
    for i in range(7):
        sample_param.append(np.random.choice(samples.iloc[:, i], 1000))
    sample_param = np.array(sample_param).T

    posterior = []
    for _, vec in enumerate(sample_param):
        _, y_model, measured_data, _ = run_model_single_parameter_node(model_long, np.array(vec))
        posterior.append(y_model)

    posterior_mean = np.mean(np.array(posterior), axis=0)

    # Create a figure
    fig = go.Figure()
    dates = model_long.get_simulation_range()
    fig.add_trace(
        go.Scatter(x=dates, y=posterior_mean, mode="lines", name="Posterior Mean")
    )
    fig.add_trace(go.Scatter(x=dates, y=measured_data, mode="lines", name="Measured Data"))

    # Update layout
    fig.update_layout(
        title=f"Posterior Sampled Using {time_series_name}, Tested on Data Containing Floods (Oldman)",
        xaxis_title="Date",
        yaxis_title="Value",
        legend_title="Time Series",
        hovermode="x unified",
        template="plotly_white",
    )

    fig.show()


def viz_short(input_file, time_series_name):
    # Construct params
    configurationObject = model_short.configurationObject
    param_lower = []
    param_upper = []
    for param in configurationObject["parameters"]:
        if param["distribution"] == "Uniform":
            param_lower.append(param["lower"])
            param_upper.append(param["upper"])
        else:
            raise NotImplementedError(
                f"Sorry, the distribution {param['distribution']} is not supported yet"
            )
    param_lower = np.array(param_lower)
    param_upper = np.array(param_upper)

    samples = pd.read_csv(f"{input_file}")

    # Sampling Max
    param_vec = []
    for i in range(len(samples.loc[0])):
        values, counts = np.unique(samples.iloc[:, i], return_counts=True)
        ind = np.argmax(counts)
        param_vec.append(values[ind])

    _, posterior_max, _, _ = run_model_single_parameter_node(model_short, param_vec)

    # Posterior Mean
    sample_param = []
    for i in range(7):
        sample_param.append(np.random.choice(samples.iloc[:, i], 1000))
    sample_param = np.array(sample_param).T

    posterior = []
    for _, vec in enumerate(sample_param):
        _, y_model, measured_data, _ = run_model_single_parameter_node(model_short, np.array(vec))
        posterior.append(y_model)

    posterior_mean = np.mean(np.array(posterior), axis=0)

    # Create a figure
    fig = go.Figure()
    dates = model_short.get_simulation_range()
    fig.add_trace(
        go.Scatter(x=dates, y=posterior_mean, mode="lines", name="Posterior Mean")
    )
    fig.add_trace(go.Scatter(x=dates, y=measured_data, mode="lines", name="Measured Data"))

    # Update layout
    fig.update_layout(
        title=f"Posterior Sampled Using {time_series_name}, Tested on Data Displaying Calmness (Oldman)",
        xaxis_title="Date",
        yaxis_title="Value",
        legend_title="Time Series",
        hovermode="x unified",
        template="plotly_white",
    )

    fig.show()


def viz_banff(input_file, time_series_name):
    # Construct params
    configurationObject = model_banff.configurationObject
    param_lower = []
    param_upper = []
    for param in configurationObject["parameters"]:
        if param["distribution"] == "Uniform":
            param_lower.append(param["lower"])
            param_upper.append(param["upper"])
        else:
            raise NotImplementedError(
                f"Sorry, the distribution {param['distribution']} is not supported yet"
            )
    param_lower = np.array(param_lower)
    param_upper = np.array(param_upper)

    samples = pd.read_csv(f"{input_file}")

    # Sampling Max
    param_vec = []
    for i in range(len(samples.loc[0])):
        values, counts = np.unique(samples.iloc[:, i], return_counts=True)
        ind = np.argmax(counts)
        param_vec.append(values[ind])

    _, posterior_max, _, _ = run_model_single_parameter_node(model_banff, param_vec)

    # Posterior Mean
    sample_param = []
    for i in range(7):
        sample_param.append(np.random.choice(samples.iloc[:, i], 1000))
    sample_param = np.array(sample_param).T

    posterior = []
    for _, vec in enumerate(sample_param):
        _, y_model, measured_data, _ = run_model_single_parameter_node(model_banff, np.array(vec))
        posterior.append(y_model)

    posterior_mean = np.mean(np.array(posterior), axis=0)

    # Create a figure
    fig = go.Figure()
    dates = model_long.get_simulation_range()
    fig.add_trace(
        go.Scatter(x=dates, y=posterior_mean, mode="lines", name="Posterior Mean")
    )
    fig.add_trace(go.Scatter(x=dates, y=measured_data, mode="lines", name="Measured Data"))

    # Update layout
    fig.update_layout(
        title=f"Posterior Sampled Using {time_series_name}, Tested on Banff",
        xaxis_title="Date",
        yaxis_title="Value",
        legend_title="Time Series",
        hovermode="x unified",
        template="plotly_white",
    )

    fig.show()


In [3]:
viz_long(all_files[0], time_series_name[0])
viz_short(all_files[0], time_series_name[0])

[HVBSASK INFO] [0] parameters: [[2.6333489706610753, 2.4051928261442788, 2.1273866731446573, 0.031072412451640555, 231.65570181750624, 0.22262518428216363, 0.04936890279707555]]
[HVBSASK INFO] [0] parameters: [array([2.62858326e+00, 2.23698151e+00, 1.94246709e+00, 1.77162298e-02,
       2.25678873e+02, 2.14545746e-01, 4.85742448e-02])]
[HVBSASK INFO] [0] parameters: [array([2.96423550e+00, 2.40395370e+00, 1.86536825e+00, 5.84554996e-03,
       2.45260569e+02, 2.62806980e-01, 4.99279589e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64157970e+00, 2.21628498e+00, 2.19967297e+00, 2.97845044e-02,
       2.18176211e+02, 2.13753828e-01, 4.96642073e-02])]
[HVBSASK INFO] [0] parameters: [array([3.04339609e+00, 3.40113047e+00, 1.86536825e+00, 1.83354775e-03,
       2.13177276e+02, 2.11733355e-01, 4.95659647e-02])]
[HVBSASK INFO] [0] parameters: [array([2.62501317e+00, 2.26495357e+00, 1.88583560e+00, 3.12268603e-02,
       2.15156684e+02, 2.19816108e-01, 4.97905423e-02])]
[HVBSASK INFO] [0] par

[HVBSASK INFO] [0] parameters: [[2.6333489706610753, 2.4051928261442788, 2.1273866731446573, 0.031072412451640555, 231.65570181750624, 0.22262518428216363, 0.04936890279707555]]
[HVBSASK INFO] [0] parameters: [array([2.86589910e+00, 1.48240578e+00, 2.60102913e+00, 5.41082114e-02,
       2.31655702e+02, 2.08761403e-01, 4.99279589e-02])]
[HVBSASK INFO] [0] parameters: [array([2.61449874e+00, 2.40196886e+00, 1.85832301e+00, 3.30152529e-02,
       2.33126408e+02, 2.25544971e-01, 4.86696520e-02])]
[HVBSASK INFO] [0] parameters: [array([2.88405154e+00, 2.22299557e+00, 1.88583560e+00, 1.72978824e-02,
       2.25972743e+02, 2.13795213e-01, 4.89896852e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64157970e+00, 2.41726679e+00, 1.87110345e+00, 4.42875490e-04,
       2.38561543e+02, 2.62806980e-01, 4.94682385e-02])]
[HVBSASK INFO] [0] parameters: [array([2.74554870e+00, 2.60009923e+00, 1.94246709e+00, 2.89239922e-03,
       2.21409246e+02, 1.91993746e-01, 4.99279589e-02])]
[HVBSASK INFO] [0] par

In [4]:
viz_long(all_files[1], time_series_name[1])
viz_short(all_files[1], time_series_name[1])

[HVBSASK INFO] [0] parameters: [[2.6246722731852223, 2.2488014752862338, 1.8803246847833888, 0.007664060279984248, 232.78262460011857, 0.21650548546941445, 0.04964223299756784]]
[HVBSASK INFO] [0] parameters: [array([2.61858352e+00, 3.36849103e+00, 1.89978643e+00, 2.43749508e-02,
       2.39569097e+02, 2.27276131e-01, 4.96720296e-02])]
[HVBSASK INFO] [0] parameters: [array([2.65383658e+00, 2.26977540e+00, 1.99107191e+00, 2.19133331e-02,
       2.30514136e+02, 2.30320808e-01, 4.97354689e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64574528e+00, 2.22316430e+00, 1.93864243e+00, 4.02355497e-02,
       2.27458622e+02, 2.18658843e-01, 4.39261672e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64401950e+00, 2.21675394e+00, 1.75111369e+00, 1.93868852e-02,
       2.29103188e+02, 2.17866318e-01, 4.73295333e-02])]
[HVBSASK INFO] [0] parameters: [array([2.85378046e+00, 2.52621873e+00, 1.93864243e+00, 1.74482789e-02,
       2.16367064e+02, 2.46531066e-01, 4.97297850e-02])]
[HVBSASK INFO] [0] par

[HVBSASK INFO] [0] parameters: [[2.6246722731852223, 2.2488014752862338, 1.8803246847833888, 0.007664060279984248, 232.78262460011857, 0.21650548546941445, 0.04964223299756784]]
[HVBSASK INFO] [0] parameters: [array([2.65275432e+00, 2.37331246e+00, 1.86642135e+00, 3.07773807e-02,
       2.32157496e+02, 2.31505899e-01, 4.87384225e-02])]
[HVBSASK INFO] [0] parameters: [array([2.38184477e+00, 2.59753920e+00, 1.95684899e+00, 2.22911267e-04,
       2.33142277e+02, 2.01042342e-01, 4.84064299e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64735733e+00, 2.21675394e+00, 1.92692047e+00, 3.32914986e-03,
       2.32318106e+02, 2.22180498e-01, 4.86667865e-02])]
[HVBSASK INFO] [0] parameters: [array([2.65815119e+00, 1.99947845e+00, 2.15608404e+00, 3.32914985e-03,
       2.37207545e+02, 2.31505899e-01, 4.96330234e-02])]
[HVBSASK INFO] [0] parameters: [array([2.62190945e+00, 2.22316430e+00, 1.72563754e+00, 2.22911267e-04,
       2.31174176e+02, 2.56930206e-01, 4.96930893e-02])]
[HVBSASK INFO] [0] par

In [5]:
viz_long(all_files[2], time_series_name[2])
viz_short(all_files[2], time_series_name[2])

[HVBSASK INFO] [0] parameters: [[2.6119082290664855, 2.2249519788204792, 1.913295263880474, 0.013886308807722292, 226.03282068708745, 0.22474278686736904, 0.04989012791490875]]
[HVBSASK INFO] [0] parameters: [array([2.63476730e+00, 2.21658759e+00, 1.92800353e+00, 7.72197922e-05,
       2.30336754e+02, 1.68214171e-01, 4.98885364e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64078610e+00, 2.05753772e+00, 1.67664562e+00, 5.94847551e-03,
       2.23079667e+02, 2.17834997e-01, 4.99147554e-02])]
[HVBSASK INFO] [0] parameters: [array([2.61289271e+00, 2.37397604e+00, 1.91266980e+00, 4.87640360e-03,
       2.31883134e+02, 2.23696732e-01, 4.98843260e-02])]
[HVBSASK INFO] [0] parameters: [array([2.58889531e+00, 2.22495198e+00, 1.94945518e+00, 2.18826050e-02,
       2.23079667e+02, 1.97262604e-01, 4.96004417e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64078610e+00, 2.22025568e+00, 2.05394791e+00, 1.20997027e-01,
       2.32164376e+02, 2.20329881e-01, 4.99147554e-02])]
[HVBSASK INFO] [0] para

[HVBSASK INFO] [0] parameters: [[2.6119082290664855, 2.2249519788204792, 1.913295263880474, 0.013886308807722292, 226.03282068708745, 0.22474278686736904, 0.04989012791490875]]
[HVBSASK INFO] [0] parameters: [array([2.60961135e+00, 2.21569709e+00, 1.92800353e+00, 8.72857840e-03,
       1.86377265e+02, 2.28187279e-01, 4.99147554e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64078610e+00, 2.33291686e+00, 1.67496783e+00, 4.90145820e-03,
       2.34146388e+02, 1.96385546e-01, 4.99244034e-02])]
[HVBSASK INFO] [0] parameters: [array([2.66572643e+00, 2.22640198e+00, 2.48814347e+00, 7.65345724e-03,
       2.01060849e+02, 2.21563036e-01, 4.99670470e-02])]
[HVBSASK INFO] [0] parameters: [array([2.39080475e+00, 2.32548156e+00, 1.87933549e+00, 1.30515917e-02,
       2.23956260e+02, 2.05604631e-01, 4.99670470e-02])]
[HVBSASK INFO] [0] parameters: [array([2.61289271e+00, 2.22495198e+00, 1.88647042e+00, 9.30194898e-03,
       2.16629038e+02, 1.96388270e-01, 4.99244034e-02])]
[HVBSASK INFO] [0] para

In [6]:
viz_long(all_files[3], time_series_name[3])
viz_short(all_files[3], time_series_name[3])

[HVBSASK INFO] [0] parameters: [[2.6203397125825356, 2.264705147281029, 1.887041609295032, 0.014525224928228175, 225.82441737748135, 0.21306536550909813, 0.04912897626130795]]
[HVBSASK INFO] [0] parameters: [array([2.63356663e+00, 2.25770192e+00, 1.63099282e+00, 1.02526723e-02,
       2.30252076e+02, 2.21269495e-01, 4.90313718e-02])]
[HVBSASK INFO] [0] parameters: [array([2.40040359e+00, 2.26470515e+00, 1.98683209e+00, 2.34459000e-02,
       2.29405320e+02, 2.09990341e-01, 4.97142016e-02])]
[HVBSASK INFO] [0] parameters: [array([2.61646735e+00, 2.16193284e+00, 1.71371353e+00, 2.60979824e-03,
       2.37303346e+02, 2.42575146e-01, 4.71709995e-02])]
[HVBSASK INFO] [0] parameters: [array([2.40040359e+00, 2.59537063e+00, 1.88704161e+00, 8.50118884e-03,
       2.30252872e+02, 2.17341826e-01, 4.98701387e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64614150e+00, 2.59929625e+00, 2.19658450e+00, 2.67732476e-02,
       2.39231831e+02, 2.28672337e-01, 4.73976560e-02])]
[HVBSASK INFO] [0] param

[HVBSASK INFO] [0] parameters: [[2.6203397125825356, 2.264705147281029, 1.887041609295032, 0.014525224928228175, 225.82441737748135, 0.21306536550909813, 0.04912897626130795]]
[HVBSASK INFO] [0] parameters: [array([2.72270787e+00, 2.23324511e+00, 2.07059541e+00, 1.61104767e-02,
       2.34480233e+02, 2.13065366e-01, 4.61293495e-02])]
[HVBSASK INFO] [0] parameters: [array([2.83614809e+00, 2.22666227e+00, 1.80300407e+00, 2.14944853e-03,
       2.21985053e+02, 2.13380911e-01, 4.91289763e-02])]
[HVBSASK INFO] [0] parameters: [array([2.28689375e+00, 2.56084664e+00, 1.88704161e+00, 4.89804754e-03,
       2.26680559e+02, 2.21626009e-01, 4.88721373e-02])]
[HVBSASK INFO] [0] parameters: [array([2.62862177e+00, 2.16193284e+00, 1.95210813e+00, 2.14944853e-03,
       2.26288044e+02, 2.13380911e-01, 4.73976560e-02])]
[HVBSASK INFO] [0] parameters: [array([2.83614809e+00, 2.29057959e+00, 2.32033171e+00, 1.61104768e-02,
       2.00282219e+02, 2.11536799e-01, 4.98036809e-02])]
[HVBSASK INFO] [0] param

In [7]:
viz_long(all_files[4], time_series_name[4])
viz_short(all_files[4], time_series_name[4])

[HVBSASK INFO] [0] parameters: [[2.6379443021411837, 2.223276540632131, 1.7622842863159391, 0.0008599336939212069, 231.45754467652984, 0.22829321169893652, 0.04967366268117743]]
[HVBSASK INFO] [0] parameters: [array([2.63794430e+00, 2.20933664e+00, 2.17116632e+00, 1.40801013e-02,
       2.56169560e+02, 2.08479825e-01, 4.99100867e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64225148e+00, 2.57918157e+00, 2.00592213e+00, 3.34919377e-03,
       2.13532408e+02, 1.78866653e-01, 4.86926619e-02])]
[HVBSASK INFO] [0] parameters: [array([2.65886632e+00, 2.39788301e+00, 1.86192772e+00, 1.67062067e-02,
       2.21458630e+02, 2.28187347e-01, 4.38118370e-02])]
[HVBSASK INFO] [0] parameters: [array([2.81318156e+00, 2.37671375e+00, 1.76228429e+00, 1.02133308e-01,
       2.56169560e+02, 2.28067664e-01, 4.99105982e-02])]
[HVBSASK INFO] [0] parameters: [array([2.61550157e+00, 2.51829204e+00, 1.74103500e+00, 8.12091889e-03,
       2.33306730e+02, 2.13166304e-01, 4.92610062e-02])]
[HVBSASK INFO] [0] par

[HVBSASK INFO] [0] parameters: [[2.6379443021411837, 2.223276540632131, 1.7622842863159391, 0.0008599336939212069, 231.45754467652984, 0.22829321169893652, 0.04967366268117743]]
[HVBSASK INFO] [0] parameters: [array([2.62943257e+00, 2.22017292e+00, 1.28701528e+00, 3.72170220e-02,
       1.99799268e+02, 2.28293212e-01, 4.90419541e-02])]
[HVBSASK INFO] [0] parameters: [array([3.07015413e+00, 2.20933664e+00, 1.82675462e+00, 2.78746057e-02,
       2.22002691e+02, 1.78866653e-01, 4.85896060e-02])]
[HVBSASK INFO] [0] parameters: [array([2.29082102e+00, 2.24646921e+00, 1.94068452e+00, 1.56705635e-02,
       2.36888244e+02, 2.32082199e-01, 4.96736627e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64225148e+00, 2.50938381e+00, 2.03852613e+00, 8.45098647e-03,
       2.11997146e+02, 2.09682866e-01, 4.03498264e-02])]
[HVBSASK INFO] [0] parameters: [array([2.82109643e+00, 2.28116878e+00, 2.03852613e+00, 3.81199091e-03,
       2.30742542e+02, 2.03334953e-01, 4.46624100e-02])]
[HVBSASK INFO] [0] par

In [8]:
viz_long(all_files[5], time_series_name[5])
viz_banff(all_files[5], time_series_name[5])

[HVBSASK INFO] [0] parameters: [[2.5809495027118774, 2.2585294489046444, 2.045050891256198, 0.0032191234447050063, 225.59419016265144, 0.21475915642489696, 0.04986537437435585]]
[HVBSASK INFO] [0] parameters: [array([2.58094950e+00, 1.04494262e+00, 1.93478679e+00, 3.21912344e-03,
       2.25182484e+02, 2.25534346e-01, 4.93922450e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64546119e+00, 2.15234634e+00, 1.83082634e+00, 2.72770302e-02,
       2.19748046e+02, 2.59847966e-01, 4.98653744e-02])]
[HVBSASK INFO] [0] parameters: [array([2.69945372e+00, 2.26583449e+00, 1.73597237e+00, 2.72770302e-02,
       2.10665330e+02, 2.14759156e-01, 4.99513700e-02])]
[HVBSASK INFO] [0] parameters: [array([2.58094950e+00, 1.91976942e+00, 1.89660144e+00, 9.12876659e-03,
       2.38102698e+02, 2.69152945e-01, 4.96381437e-02])]
[HVBSASK INFO] [0] parameters: [array([2.30209155e+00, 2.39829472e+00, 1.73597237e+00, 2.78396407e-02,
       2.25594190e+02, 2.55814999e-01, 4.99566554e-02])]
[HVBSASK INFO] [0] par

[HVBSASK INFO] [0] parameters: [[2.5809495027118774, 2.2585294489046444, 2.045050891256198, 0.0032191234447050063, 225.59419016265144, 0.21475915642489696, 0.04986537437435585]]
[HVBSASK INFO] [0] parameters: [array([1.12639984e+00, 2.21259956e+00, 1.77235557e+00, 1.96265853e-02,
       2.39768548e+02, 2.13518981e-01, 4.99566554e-02])]
[HVBSASK INFO] [0] parameters: [array([2.97994478e+00, 2.20431914e+00, 2.47164698e+00, 1.36935426e-03,
       2.36090294e+02, 2.03977621e-01, 4.99003075e-02])]
[HVBSASK INFO] [0] parameters: [array([2.59745351e+00, 2.63971168e+00, 1.89660144e+00, 5.25380013e-03,
       2.37826922e+02, 2.32095056e-01, 4.99076066e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64546119e+00, 1.15556723e+00, 1.88609255e+00, 7.03157844e-02,
       2.37826922e+02, 2.12911453e-01, 4.78589076e-02])]
[HVBSASK INFO] [0] parameters: [array([2.30221627e+00, 1.97031430e+00, 1.85520136e+00, 2.11997788e-02,
       1.71011912e+02, 2.07118590e-01, 4.55946493e-02])]
[HVBSASK INFO] [0] par

In [9]:
viz_long(all_files[6], time_series_name[6])
viz_short(all_files[6], time_series_name[6])

[HVBSASK INFO] [0] parameters: [[2.753750248136408, 2.5782314299316025, 1.8514289707749885, 0.0028900056462653014, 231.6326501873791, 0.19751727290583768, 0.049039447914878874]]
[HVBSASK INFO] [0] parameters: [array([2.75819314e+00, 2.53185378e+00, 2.00102771e+00, 1.02353484e-02,
       2.34940454e+02, 2.04589588e-01, 4.94663305e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64318756e+00, 3.22762998e+00, 2.11027475e+00, 4.97088921e-02,
       2.20525094e+02, 2.03579824e-01, 4.80728898e-02])]
[HVBSASK INFO] [0] parameters: [array([2.98359082e+00, 2.52770815e+00, 2.01540195e+00, 1.42626850e-02,
       2.41494814e+02, 2.21575763e-01, 4.94663305e-02])]
[HVBSASK INFO] [0] parameters: [array([2.76122759e+00, 3.22762998e+00, 2.00243408e+00, 2.20137560e-02,
       2.30721221e+02, 2.23290422e-01, 4.96934147e-02])]
[HVBSASK INFO] [0] parameters: [array([2.72179496e+00, 2.35286520e+00, 1.96530950e+00, 1.16884564e-02,
       2.26536549e+02, 2.29375857e-01, 4.99796596e-02])]
[HVBSASK INFO] [0] par

[HVBSASK INFO] [0] parameters: [[2.753750248136408, 2.5782314299316025, 1.8514289707749885, 0.0028900056462653014, 231.6326501873791, 0.19751727290583768, 0.049039447914878874]]
[HVBSASK INFO] [0] parameters: [array([2.95179969e+00, 2.42374557e+00, 1.85142897e+00, 1.44458202e-02,
       2.28343196e+02, 2.16738552e-01, 4.81362053e-02])]
[HVBSASK INFO] [0] parameters: [array([2.33977338e+00, 2.53643268e+00, 2.34010705e+00, 2.04856569e-02,
       2.01721840e+02, 2.18754864e-01, 4.98315909e-02])]
[HVBSASK INFO] [0] parameters: [array([2.74949346e+00, 2.33834016e+00, 2.00102771e+00, 4.95624393e-03,
       2.29747848e+02, 1.97517273e-01, 4.96934147e-02])]
[HVBSASK INFO] [0] parameters: [array([2.31633388e+00, 2.35286520e+00, 1.82787750e+00, 1.16884564e-02,
       2.34940454e+02, 2.21575763e-01, 4.40622554e-02])]
[HVBSASK INFO] [0] parameters: [array([2.75136264e+00, 2.53185378e+00, 1.85142897e+00, 6.94597880e-03,
       2.31632650e+02, 2.03836617e-01, 4.99743709e-02])]
[HVBSASK INFO] [0] par

In [10]:
viz_long(all_files[7], time_series_name[7])
viz_short(all_files[7], time_series_name[7])

[HVBSASK INFO] [0] parameters: [[2.670675646173218, 2.329554676705637, 2.1151929913046366, 0.006550436854419892, 228.96304289041848, 0.22216502797857424, 0.04811658175988387]]
[HVBSASK INFO] [0] parameters: [array([2.70670566e+00, 2.19658702e+00, 2.05495846e+00, 1.74685337e-02,
       2.20847318e+02, 2.21306035e-01, 4.94538664e-02])]
[HVBSASK INFO] [0] parameters: [array([2.63694145e+00, 2.37273057e+00, 2.05495846e+00, 5.38148845e-02,
       2.28963043e+02, 2.00437873e-01, 4.89816891e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64956227e+00, 2.21101542e+00, 1.51940934e+00, 3.73699477e-03,
       2.20847318e+02, 2.00599226e-01, 4.95138685e-02])]
[HVBSASK INFO] [0] parameters: [array([2.63694145e+00, 2.23930842e+00, 1.73614719e+00, 4.26741959e-02,
       2.21423274e+02, 2.15302555e-01, 4.92248002e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64907002e+00, 2.48411286e+00, 1.82713595e+00, 6.55043685e-03,
       2.19963340e+02, 2.15834581e-01, 4.99454211e-02])]
[HVBSASK INFO] [0] param

[HVBSASK INFO] [0] parameters: [[2.670675646173218, 2.329554676705637, 2.1151929913046366, 0.006550436854419892, 228.96304289041848, 0.22216502797857424, 0.04811658175988387]]
[HVBSASK INFO] [0] parameters: [array([3.03979139e+00, 2.19658702e+00, 1.78136267e+00, 1.84551836e-02,
       2.23815267e+02, 1.98033900e-01, 4.99024152e-02])]
[HVBSASK INFO] [0] parameters: [array([1.06206690e+00, 9.83185799e-01, 1.88080650e+00, 4.24110410e-03,
       2.38108075e+02, 2.13250036e-01, 4.99024152e-02])]
[HVBSASK INFO] [0] parameters: [array([2.63694145e+00, 2.22639078e+00, 1.90694591e+00, 3.33725870e-02,
       2.29898241e+02, 2.26940222e-01, 4.78830734e-02])]
[HVBSASK INFO] [0] parameters: [array([3.16389936e+00, 2.21842336e+00, 2.00116964e+00, 6.90682967e-02,
       2.20524425e+02, 2.20058360e-01, 4.94538664e-02])]
[HVBSASK INFO] [0] parameters: [array([2.70819956e+00, 2.26636125e+00, 2.00644188e+00, 2.57433077e-02,
       2.36100911e+02, 2.12892385e-01, 4.30825987e-02])]
[HVBSASK INFO] [0] param

In [11]:
viz_long(all_files[8], time_series_name[8])
viz_short(all_files[8], time_series_name[8])

[HVBSASK INFO] [0] parameters: [[2.384779705524455, 2.0045573108084374, 1.9851176349674524, 0.0026707524633968064, 223.64941122221745, 0.22456757613056463, 0.04979347779604481]]
[HVBSASK INFO] [0] parameters: [array([2.62704346e+00, 1.93839346e+00, 2.35032111e+00, 1.44490374e-02,
       2.31129112e+02, 2.37803899e-01, 4.61338696e-02])]
[HVBSASK INFO] [0] parameters: [array([2.62334406e+00, 1.93839346e+00, 1.88493238e+00, 1.44490374e-02,
       2.28181633e+02, 2.14699692e-01, 4.88940628e-02])]
[HVBSASK INFO] [0] parameters: [array([2.75566659e+00, 2.24508260e+00, 1.91707252e+00, 2.02296041e-02,
       2.31733575e+02, 2.24567576e-01, 4.97995662e-02])]
[HVBSASK INFO] [0] parameters: [array([2.60239800e+00, 2.20634998e+00, 1.88493238e+00, 2.25600228e-02,
       2.38299894e+02, 2.24567576e-01, 4.44922981e-02])]
[HVBSASK INFO] [0] parameters: [array([2.53149425e+00, 2.29547745e+00, 1.85898561e+00, 2.25600228e-02,
       2.21013141e+02, 2.24567576e-01, 4.59538343e-02])]
[HVBSASK INFO] [0] par

[HVBSASK INFO] [0] parameters: [[2.384779705524455, 2.0045573108084374, 1.9851176349674524, 0.0026707524633968064, 223.64941122221745, 0.22456757613056463, 0.04979347779604481]]
[HVBSASK INFO] [0] parameters: [array([2.61159658e+00, 2.23913677e+00, 1.80934402e+00, 1.21803677e-02,
       2.41565330e+02, 2.10838564e-01, 4.91116798e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64647650e+00, 1.93839346e+00, 1.87479187e+00, 2.35914338e-02,
       2.33427121e+02, 2.37803899e-01, 4.90183229e-02])]
[HVBSASK INFO] [0] parameters: [array([2.64948299e+00, 2.21756175e+00, 1.88493238e+00, 2.35914338e-02,
       2.30457805e+02, 2.20481342e-01, 4.44922981e-02])]
[HVBSASK INFO] [0] parameters: [array([2.58448247e+00, 1.96243512e+00, 1.62540361e+00, 2.25600228e-02,
       2.25929286e+02, 2.23497641e-01, 4.96416744e-02])]
[HVBSASK INFO] [0] parameters: [array([2.63658292e+00, 2.20634998e+00, 2.46183401e+00, 2.68440793e-02,
       2.38299894e+02, 2.24567576e-01, 4.93867523e-02])]
[HVBSASK INFO] [0] par